In [1]:
import pickle
import pandas as pd
import torch
from torch import nn
from sklearn.preprocessing import LabelEncoder
from concurrent.futures import ProcessPoolExecutor
import numpy as np
from operator import itemgetter
THREADS = 16
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import f1_score
import time
import torch.nn.functional as F
loss_func = torch.nn.MSELoss()

In [2]:
ratings = pd.read_pickle('small_ratings_movielens.pkl')
films = pd.read_pickle('small_films_movielens.pkl')

In [3]:
row = []
for mid,haha in ratings.items():
    for info in haha:
        info['movie'] = mid
        row.append(info)
df_ratings = pd.DataFrame(row)
row = []
for mid,haha in films.items():
    haha['movie'] = mid
    row.append(haha)
df_movie = pd.DataFrame(row)

In [4]:
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"

In [5]:
final = pd.merge(df_movie,df_ratings,on='movie')
a = final['user_id'].value_counts()[final['user_id'].value_counts() >= 10]
final = final[final['user_id'].isin(list(a.index))]
final.index = range(len(final))
hehe = final.copy()
del hehe['title']
del hehe['user_rating_date']

In [6]:
movie = dict()
for i in range(df_movie.shape[0]):
    m = df_movie['movie'][i]
    movie.setdefault(m,dict())
    movie[m]['director'] = df_movie['director'][i]
    movie[m]['genre'] = df_movie['genre'][i]
    movie[m]['actors'] = df_movie['actors'][i]
    movie[m]['title'] = df_movie['title'][i]

In [7]:
def map_aspect_values_to_movies(x):
    (film, meta), aspect = x
    aspects = dict()
    if aspect == "director" and type(meta[aspect]) is str:
        aspects[meta[aspect]] = 1
    else:
        for g in meta[aspect]:
            aspects[g] = 1
    return film, meta, aspects


def dict_movie_aspect(paper_films, aspect):
    paper_films_aspect_prepended = map(
        lambda e: (e, aspect), list(paper_films.items()))
    aspect_dict = dict()
    with ProcessPoolExecutor(max_workers=THREADS) as executor:
        results = executor.map(map_aspect_values_to_movies,
                               paper_films_aspect_prepended)
    for film, meta, aspects in results:
        aspect_dict[film + "_" + meta["title"]] = aspects

    return aspect_dict

In [8]:
movie_genres = dict_movie_aspect(movie, "genre")
movie_directors = dict_movie_aspect(movie,'director')
movie_actors = dict_movie_aspect(movie,'actors')
actors = pd.DataFrame.from_dict(movie_actors,dtype = 'int64',orient = 'index').T.replace(np.nan, 0).index
directors = pd.DataFrame.from_dict(movie_directors,dtype = 'int64',orient = 'index').T.replace(np.nan, 0).index
genres = pd.DataFrame.from_dict(movie_genres,dtype = 'int64',orient = 'index').T.replace(np.nan, 0).index

<ipython-input-8-4af81307f982>:4: FutureWarning: In a future version, passing float-dtype values containing NaN and an integer dtype will raise IntCastingNaNError (subclass of ValueError) instead of silently ignoring the passed dtype. To retain the old behavior, call Series(arr) or DataFrame(arr) without passing a dtype.
  actors = pd.DataFrame.from_dict(movie_actors,dtype = 'int64',orient = 'index').T.replace(np.nan, 0).index
<ipython-input-8-4af81307f982>:5: FutureWarning: In a future version, passing float-dtype values containing NaN and an integer dtype will raise IntCastingNaNError (subclass of ValueError) instead of silently ignoring the passed dtype. To retain the old behavior, call Series(arr) or DataFrame(arr) without passing a dtype.
  directors = pd.DataFrame.from_dict(movie_directors,dtype = 'int64',orient = 'index').T.replace(np.nan, 0).index
<ipython-input-8-4af81307f982>:6: FutureWarning: In a future version, passing float-dtype values containing NaN and an integer dtype

In [9]:
actors_dict = dict(zip(actors, range(len(actors))))
directors_dict = dict(zip(directors, range(
    len(actors), len(actors) + len(directors))))
genres_dict = dict(zip(genres, range(
    len(actors) + len(directors), len(actors) + len(directors) + len(genres))))
# max(actors_dict.values()),max(directors_dict.values()),max(genres_dict.values())

In [10]:
def change_director(x):
    qunima = itemgetter(*x)(directors_dict)
    if type(qunima) == int:
        return [qunima]
    else:
        return change_list(qunima)


def change_genre(x):
    qunima = itemgetter(*x)(genres_dict)
    if type(qunima) == int:
        return [qunima]
    else:
        return change_list(qunima)


def change_actor(x):
    qunima = itemgetter(*x)(actors_dict)
    if type(qunima) == int:
        return [qunima]
    else:
        return list(qunima)


def change_list(x):
    return list(x)

In [11]:
hehe = final.copy()
del hehe['title']
del hehe['user_rating_date']

In [12]:
hehe['director'] = hehe['director'].map(change_director)
hehe['actors'] = hehe['actors'].map(change_actor)
hehe['genre'] = hehe['genre'].map(change_genre)

In [13]:
hehe = hehe[['user_id','movie','actors','director','genre','user_rating']]
hehe['user_rating'] = hehe['user_rating'].astype('float')

In [14]:
le = LabelEncoder()
y = le.fit_transform(hehe['user_id'])
hehe['user_id'] = y

y = le.fit_transform(hehe['movie'])
hehe['movie'] = y


In [15]:
print("The number of aspects is {}".format(max(genres_dict.values()) + 1))
print("The number of users is {}".format(max(hehe['user_id'])+1))

The number of aspects is 22428
The number of users is 610


In [16]:
from tqdm import tqdm
from torch.nn import LeakyReLU
leaky = LeakyReLU(0.2)

def calculate_score(x, users, aspects):
    niubi = []
    # users: 128 * 8
    first = x.index[0]
    val_base = x[first]
    actor_base = torch.LongTensor(val_base)
    actors_base = aspects(actor_base)  # 3 * 8
    #actors_base = actors_base + items[first % 128].unsqueeze(1)
    #actors_base = F.dropout(actors_base, p=rate, training=True)
    pre_rating = torch.mm(actors_base, users[first].unsqueeze(1))
    niubi.append(pre_rating)
    pre_rating = pre_rating / pre_rating.shape[0]
    pre_rating = pre_rating.sum(0)
    for i in x.index[1:]:
        val = x[i]
        actor = torch.LongTensor(val)
        actors = aspects(actor)
        pre_ra = torch.mm(actors, users[i].unsqueeze(1))
        niubi.append(pre_ra)
        actors_f = pre_ra / pre_ra.shape[0]
        actors_f = actors_f.sum(0)
        pre_rating = torch.cat((pre_rating, actors_f))
    return pre_rating, niubi


class aspect_augumentation(nn.Module):
    def __init__(self, n_users, n_entity, n_rk, n_factors):
        super(aspect_augumentation, self).__init__()
        self.n_users = n_users
        self.n_entity = n_entity
        self.n_rk = n_rk
        self.n_factors = n_factors
        self.user_factors = torch.nn.Embedding(n_users, n_factors)
        self.entity_factors = torch.nn.Embedding(n_entity, n_factors)
        self.relation_k = torch.nn.Embedding(n_factors, n_rk)

    def forward(self, user_id, actors_id, directors_id, genres_id):
        '''
        user_factors: n_users * 64
        entity_factors: n_entity * 64
        relation_k: 64 * 3
        '''
        
        users = self.user_factors(user_id)  # 128 * 8
        aspects = self.entity_factors  # n_entity * 8
        users = F.dropout(users, p=rate, training=self.training)
        scores = torch.matmul(users, F.dropout(self.relation_k.weight, p=rate, training=self.training))  # 128 * 3
        scores = leaky(scores)
        m=torch.nn.Softmax(dim=1)  # 128 * 3
        scores=m(scores)  # 128 * 3

        '''
        Compute the importance of each aspects
        '''
        scores_actors=scores[:, 0] # 128,
        scores_directors=scores[:, 1] # 128,
        scores_genres=scores[:, 2] # 128,

        '''
        Compute the contribution of each aspects
        '''
        contribute_actors,niubi_act=calculate_score(
            actors_id, users,aspects)
        contribute_directors, niubi_dir=calculate_score(
            directors_id, users,aspects)
        contribute_genres, niubi_gen=calculate_score(
            genres_id, users, aspects)

        '''
        Compute the final predictions
        '''
        importance_sum=scores_actors + scores_directors + scores_genres
        prediction_sum=contribute_actors * scores_actors + contribute_directors * scores_directors + contribute_genres * scores_genres
        prediction=prediction_sum / importance_sum
        cnm = [niubi_act,niubi_dir,niubi_gen]

        return prediction, scores, contribute_actors, contribute_directors, contribute_genres,cnm

In [17]:
from tqdm import tqdm
from torch.nn import LeakyReLU
leaky = LeakyReLU(0.2)

def calculate_score(x, users, aspects,batch_size):
    niubi = []
    # users: 128 * 8
    first = x.index[0]
    val_base = x[first]
    actor_base = torch.LongTensor(val_base)
    actors_base = aspects(actor_base)  # 3 * 8
    #actors_base = actors_base + items[first % 128].unsqueeze(1)
    #actors_base = F.dropout(actors_base, p=rate, training=True)
    pre_rating = torch.mm(actors_base, users[first].unsqueeze(1))
    niubi.append(pre_rating)
    pre_rating = pre_rating / pre_rating.shape[0]
    pre_rating = pre_rating.sum(0)
    for i in x.index[1:]:
        val = x[i]
        actor = torch.LongTensor(val)
        actors = aspects(actor)
        pre_ra = torch.mm(actors, users[i].unsqueeze(1))
        niubi.append(pre_ra)
        actors_f = pre_ra / pre_ra.shape[0]
        actors_f = actors_f.sum(0)
        pre_rating = torch.cat((pre_rating, actors_f))
    return pre_rating, niubi


class aspect_augumentation(nn.Module):
    def __init__(self, n_users, n_entity, n_rk, n_factors):
        super(aspect_augumentation, self).__init__()
        self.n_users = n_users
        self.n_entity = n_entity
        self.n_rk = n_rk
        self.n_factors = n_factors
        self.user_factors = torch.nn.Embedding(n_users, n_factors)
        self.entity_factors = torch.nn.Embedding(n_entity, n_factors)
        self.relation_k = torch.nn.Embedding(n_factors, n_rk)

    def forward(self, user_id, actors_id, directors_id, genres_id, batch_size):
        '''
        user_factors: n_users * 64
        entity_factors: n_entity * 64
        relation_k: 64 * 3
        '''
        
        users = self.user_factors(user_id)  # 128 * 8
        aspects = self.entity_factors  # n_entity * 8
        users = F.dropout(users, p=rate, training=self.training)
        scores = torch.matmul(users, F.dropout(self.relation_k.weight, p=rate, training=self.training))  # 128 * 3
        scores = leaky(scores)
        m=torch.nn.Softmax(dim=1)  # 128 * 3
        scores=m(scores)  # 128 * 3

        '''
        Compute the importance of each aspects
        '''
        scores_actors=scores[:, 0] # 128,
        scores_directors=scores[:, 1] # 128,
        scores_genres=scores[:, 2] # 128,

        '''
        Compute the contribution of each aspects
        '''
        contribute_actors,niubi_act=calculate_score(
            actors_id, users,aspects,batch_size)
        contribute_directors, niubi_dir=calculate_score(
            directors_id, users,aspects,batch_size)
        contribute_genres, niubi_gen=calculate_score(
            genres_id, users, aspects,batch_size)

        '''
        Compute the final predictions
        '''
        importance_sum=scores_actors + scores_directors + scores_genres
        prediction_sum=contribute_actors * scores_actors + contribute_directors * scores_directors + contribute_genres * scores_genres
        prediction=prediction_sum / importance_sum
        cnm = [niubi_act,niubi_dir,niubi_gen]

        return prediction, scores, contribute_actors, contribute_directors, contribute_genres,cnm

In [18]:
def RMSE(data, model,batch_size):
    users_index = data.iloc[:, 0].values
    users = torch.LongTensor(users_index).to(DEVICE)
    actors_id = data.iloc[:, 2]
    directors_id = data.iloc[:, 3]
    genres_id = data.iloc[:, 4]
    rating = torch.FloatTensor(
        data.iloc[:, 5].values).to(DEVICE)
    prediction,scores,contribute_actors,contribute_directors,contribute_genres,cnm = model(users,actors_id, directors_id, genres_id,batch_size)
    rmse = loss_func(prediction, rating)
    mae = torch.nn.L1Loss()(prediction, rating)
    
    return rmse ** 0.5,mae, cnm

In [19]:
def train(lr, dim, reg, batch_size, num_epochs, data, test):
    model = aspect_augumentation(610, 22428, 3, dim).to(DEVICE)
    optimizer = torch.optim.Adam(params=model.parameters(), lr=lr,weight_decay=reg)
    scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
        optimizer, mode='min', factor=0.5, patience=10, threshold_mode='abs',threshold = 0.005)
    for epoch in range(num_epochs):
        model.train()
        t1 = time.time()
        num_example = len(data)
        indices = list(range(num_example))
        for i in tqdm(range(0, num_example, batch_size)):
            optimizer.zero_grad()
            indexs = indices[i:min(i+batch_size, num_example)]
            users_index = data.iloc[:, 0].loc[indexs].values
            users = torch.LongTensor(users_index).to(DEVICE)
            actors_id = data.iloc[:, 2].loc[indexs]
            actors_id.index = range(len(actors_id))
            directors_id = data.iloc[:, 3].loc[indexs]
            directors_id.index = range(len(directors_id))
            genres_id = data.iloc[:, 4].loc[indexs]
            genres_id.index = range(len(genres_id))
            rating = torch.FloatTensor(
                data.iloc[:, 5].loc[indexs].values).to(DEVICE)
            prediction, scores, contribute_actors, contribute_directors, contribute_genres,cnm = model(
                users, actors_id, directors_id, genres_id,batch_size)

            err = loss_func(prediction, rating) 
            err.backward()
            optimizer.step()
        t2 = time.time()
        rmse, mae,cnm = RMSE(test, model,batch_size)
        scheduler.step(rmse)
        print("Epoch: ", epoch, " Loss: ", err, " RMSE in test set:",
              rmse, "MAE in test set: ", mae)
        print("Time consumed is:", t2-t1)
    return rmse, mae, model, cnm

In [20]:
hehe_test = hehe.copy()
df_empty = pd.DataFrame(columns=['user_id', 'movie', 'actors', 'director', 'genre', 'user_rating'])
for user in set(hehe_test['user_id']):
    mean_rating = hehe_test[hehe_test['user_id'] == user]['user_rating'].mean()
    pos_df = hehe_test[hehe_test['user_id'] == user]
    pos_df = pos_df[pos_df['user_rating'] > mean_rating]
    pos_df = pos_df.iloc[-1:]
    index_to_remove = list(pos_df.iloc[-1:].index)
    df_empty = df_empty.append(pos_df)
    hehe_test.drop(index = index_to_remove)
    
    

<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty =

<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty =

<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty =

<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty =

<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty =

...

<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty =

<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty =

<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty =

<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty =

<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty = df_empty.append(pos_df)
<ipython-input-20-a3df207afc2d>:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_empty =

In [22]:
hehe_test.shape, df_empty.shape
hehe_test.to_csv('new_models/train.csv',index=False)
df_empty.to_csv('new_models/test.csv',index=False)

In [23]:
hehe_test.shape, df_empty.shape

((100378, 6), (609, 6))

In [24]:
df_empty['user_id'] = df_empty['user_id'].astype('int')
df_empty['user_rating'] = df_empty['user_rating'].astype('float')

In [25]:
df_empty['movie'] = df_empty['movie'].astype('int')

In [26]:
hehe_test.index = range(len(hehe_test))
df_empty.index = range(len(df_empty))

In [27]:
def grid(lrs, dims, regs, batch_sizes, num_epochs, data, test):
    res = []
    models = []
    qnm = []
    for lr in lrs:
        for dim in dims:
            for reg in regs:
                for batch_size in batch_sizes:
                    rmse, mae, model,cnm = train(
                        lr, dim, reg, batch_size, num_epochs, data, test)
                    res.append(rmse)
                    res.append(mae)

                    models.append(model)
                    state = { 'model': model.state_dict()}   
                    torch.save(state, '/home/jinfeng/Downloads/doctorant/Conférences/dsaa/argumrntative/KR2020-Aspect-Item-Recommender-System-master/data/MOVIELENS/ml-latest-small/new_models/model_' + str(lr) + '_' + str(dim) + '_' + str(reg) + '_' + str(batch_size) + '.pkl')
                    qnm.append(cnm)
    return res, models,qnm

In [ ]:
rate = 0.0
lrs = [1e-2]
dims = [32]
regs = [1e-7]
batch_sizes = [256,512]
num_epochs = 70
res_reg, models_reg,qnm = grid(lrs,dims,regs,batch_sizes,num_epochs,hehe_test,df_empty)

In [36]:
#conding=utf8  
import os 

path = "/home/jinfeng/Downloads/doctorant/Conférences/dsaa/argumrntative/KR2020-Aspect-Item-Recommender-System-master/data/MOVIELENS/ml-latest-small/new_models/models/" 
def get_file_name(path):
    for file in os.listdir(path):
        lr = file.split('_')[1]
        dim = file.split('_')[2]
        reg = file.split('_')[3]
        
        model = aspect_augumentation(610, 22428, 3, int(file.split('_')[2])).to(DEVICE)
        load_params = torch.load('/home/jinfeng/Downloads/doctorant/Conférences/dsaa/argumrntative/KR2020-Aspect-Item-Recommender-System-master/data/MOVIELENS/ml-latest-small/new_models/models/' + file)['model']
        model_params = model.state_dict()
        same_parsms = {k: v for k, v in load_params.items() if k in model_params.keys()}
        model_params.update(same_parsms)

        model.load_state_dict(model_params)
        rmse, mae,cnm = RMSE(df_empty, model,1)
        print("Learning rate: ",lr, "dimension of vector: ", dim, "Regularization rate: ", reg)
        print(" RMSE in test set:",
              rmse, "MAE in test set: ", mae)

In [38]:
get_file_name(path)

Learning rate:  0.01 dimension of vector:  32 Regularization rate:  1e-07
 RMSE in test set: tensor(0.4070, grad_fn=<PowBackward0>) MAE in test set:  tensor(0.2860, grad_fn=<L1LossBackward0>)
Learning rate:  0.01 dimension of vector:  32 Regularization rate:  1e-07
 RMSE in test set: tensor(0.2176, grad_fn=<PowBackward0>) MAE in test set:  tensor(0.1507, grad_fn=<L1LossBackward0>)


In [39]:
df_sum = hehe.copy()
movie_set = set(df_sum['movie'])
movie = df_sum[['movie','actors','director','genre']].loc[df_sum[['movie','actors','director','genre']].astype(str).drop_duplicates().index]
movie.index = range(len(movie))
movie = movie[['movie','actors','director','genre']].loc[movie[['movie','actors','director','genre']].astype(str).drop_duplicates().index]

In [40]:
def dic_order_value_and_get_key(dicts, count):
    final_result = []
    sorted_dic = sorted([(k, v) for k, v in dicts.items()], reverse=True)
    tmp_set = set()
    for item in sorted_dic:
        tmp_set.add(item[1])
    for list_item in sorted(tmp_set, reverse=True)[:count]:
        for dic_item in sorted_dic:
            if dic_item[1] == list_item:
                final_result.append(dic_item[0])
    return final_result

In [41]:
user_item = {}
user_item_neg = {}

for user in set(hehe['user_id']):
    if user not in user_item:
        mean_rating = hehe_test[hehe_test['user_id'] == user]['user_rating'].mean()
        pos_df = hehe_test[hehe_test['user_id'] == user]
        pos_df = pos_df[pos_df['user_rating'] > mean_rating]
        user_item[user] = set(pos_df['user_id'].values)
for user,pos_item_set in user_item.items():
    unwatched_set = movie_set - pos_item_set
    if user not in user_item_neg:
        user_item_neg[user] = set()
    user_item_neg[user] = set(np.random.choice(list(unwatched_set), size=100, replace=False))
    

In [6]:
(0.5318-0.1507)/0.5318

0.7166227905227529

In [42]:
num_i = 101
def get_prediction_list(model,user, target, actors_id, directors_id, genres_id,k):
    item_neg = user_item_neg[user]
    movie_rec = movie[movie['movie'].isin(item_neg)]
    movie_rec.index = range(1, len(movie_rec)+1)
    movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
    user = np.array([user] * num_i)
    user = torch.LongTensor(user).to(DEVICE)
    actors_id = movie_rec.iloc[:, 1]
    directors_id = movie_rec.iloc[:, 2]
    genres_id = movie_rec.iloc[:, 3]
    prediction, scores, contribute_actors, contribute_directors, contribute_genres, cnm = model(
        user, actors_id, directors_id, genres_id,1)
    prediction = prediction.detach().numpy()
    prediction = np.maximum(prediction, np.ones(num_i) * 0)  # bound the lower values
    prediction = np.minimum(prediction, np.ones(num_i) * 5)
    prediction_dict = dict(zip(movie_rec['movie'].values, prediction))
    top_k = dic_order_value_and_get_key(prediction_dict,k)
    return top_k,prediction_dict

In [44]:
model = aspect_augumentation(610, 22428, 3, 32).to(DEVICE)
load_params = torch.load(path + 'model_0.01_32_1e-07_256.pkl')['model']
model_params = model.state_dict()
same_parsms = {k: v for k, v in load_params.items()
               if k in model_params.keys()}
model_params.update(same_parsms)

model.load_state_dict(model_params)

<All keys matched successfully>

In [45]:
import math
def hr_ndcg(data,model):
    hr1 = 0.0
    ndcg1 = 0.0
    hr2 = 0.0
    ndcg2 = 0.0
    test_eva_dict = df_empty.to_dict('records')
    for row in test_eva_dict[:]:
        user = row['user_id']
        target = row['movie']
        actors_id = row['actors']
        directors_id = row['director']
        genres_id = row['genre']
        
        
        recommended_item_10,_ = get_prediction_list(model,user,target,actors_id,directors_id,genres_id,10)
        recommended_item_20,_ = get_prediction_list(model,user,target,actors_id,directors_id,genres_id,20)
        if target in recommended_item_10:
            hr1 +=1
            posi = recommended_item_10.index(target)
            ndcg1 += 1 / math.log(posi + 2,2)
        if target in recommended_item_20:
            hr2 +=1
            posi = recommended_item_20.index(target)
            ndcg2 += 1 / math.log(posi + 2,2)
    return hr1 / data.shape[0], ndcg1 / data.shape[0],hr2 / data.shape[0], ndcg2 / data.shape[0]
        

In [46]:
hr_ndcg(df_empty,model)

<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when cr

<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc

<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc

<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when cr

<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when cr

...

<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when cr

<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when cr

<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when cr

<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-42-839e61605c10>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc

(0.6781609195402298,
 0.2791758708916008,
 0.916256157635468,
 0.33609187729331474)

In [47]:
from surprise import SVD,KNNBaseline,KNNWithZScore, NMF, SlopeOne, CoClustering
from surprise import Dataset
from surprise import accuracy
from surprise.model_selection import train_test_split
from surprise import Reader
from surprise.model_selection import cross_validate

reader = Reader(rating_scale=(1, 5))
train = Dataset.load_from_df(hehe_test[['user_id', 'movie', 'user_rating']], reader)
test = Dataset.load_from_df(df_empty[['user_id', 'movie', 'user_rating']], reader)
train = train.build_full_trainset()
test = test.build_full_trainset()
test = test.build_testset()

In [48]:
for algo in [SVD,KNNBaseline,KNNWithZScore, NMF, SlopeOne, CoClustering]:
    algo = algo()
    algo.fit(train)
    predictions = algo.test(test)
    accuracy.rmse(predictions)
    accuracy.mae(predictions)

RMSE: 0.6404
MAE:  0.5231
Estimating biases using als...
Computing the msd similarity matrix...
Done computing similarity matrix.
RMSE: 0.6014
MAE:  0.4570
Computing the msd similarity matrix...
Done computing similarity matrix.
RMSE: 0.6285
MAE:  0.4666
RMSE: 0.5785
MAE:  0.4329
RMSE: 0.6353
MAE:  0.4915


<ipython-input-48-b5ba48e4e7ab>:3: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  algo.fit(train)


RMSE: 0.8096
MAE:  0.6190


In [49]:
num_i = 100
def get_prediction_list(model,user, target,k):
    user1 = user
    item_neg = user_item_neg[user1]
    movie_rec = movie[movie['movie'].isin(item_neg)]
    movie_rec.index = range(1, len(movie_rec)+1)
    user = np.array([user1] * num_i)
    movie_rec['user'] = np.array(user)
    movie_rec['rating'] = 1.0
    movie_rec = movie_rec[['user','movie','rating']]
    movie_rec.loc[0] = np.array([user1, target, 1.0])
    movie_rec1 = Dataset.load_from_df(movie_rec[['user','movie','rating']], reader)
    test = movie_rec1.build_full_trainset()
    test = test.build_testset()
    predictions = model.test(test)
    predictions_list = []
    for uid, iid, true_r, est, _ in predictions:
        predictions_list.append(est)
    prediction_dict = dict(zip(movie_rec['movie'].values, predictions_list))
    top_k = dic_order_value_and_get_key(prediction_dict,k)
    return top_k

In [50]:
import math
def hr_ndcg(data,model):
    hr1 = 0.0
    ndcg1 = 0.0
    hr2 = 0.0
    ndcg2 = 0.0
    test_eva_dict = df_empty.to_dict('records')
    for row in test_eva_dict[:]:
        user = row['user_id']
        target = row['movie']
        
        
        
        recommended_item_10 = get_prediction_list(model,user,target,10)
        recommended_item_20 = get_prediction_list(model,user,target,20)
        if target in recommended_item_10:
            hr1 +=1
            posi = recommended_item_10.index(target)
            ndcg1 += 1 / math.log(posi + 2,2)
        if target in recommended_item_20:
            hr2 +=1
            posi = recommended_item_20.index(target)
            ndcg2 += 1 / math.log(posi + 2,2)
    print(algo)
    print(hr1 / data.shape[0], ndcg1 / data.shape[0],hr2 / data.shape[0], ndcg2 / data.shape[0])
    return hr1 / data.shape[0], ndcg1 / data.shape[0],hr2 / data.shape[0], ndcg2 / data.shape[0]

In [51]:
res = []
for algo in [SVD,KNNBaseline,KNNWithZScore, NMF, SlopeOne, CoClustering]:
    algo = algo()
    algo.fit(train)
    predictions = algo.test(test)
    accuracy.rmse(predictions)
    accuracy.mae(predictions)
    hr10,ndcg10,hr20,ndcg20 = hr_ndcg(df_empty,algo)
    res.append([hr10, ndcg10, hr20, ndcg20])

RMSE: 0.6482
MAE:  0.5329


<ipython-input-49-75e65edfc8ed>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec['user'] = np.array(user)
<ipython-input-49-75e65edfc8ed>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec['rating'] = 1.0
<ipython-input-49-75e65edfc8ed>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = n

<ipython-input-49-75e65edfc8ed>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([user1, target, 1.0])
<ipython-input-49-75e65edfc8ed>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec['user'] = np.array(user)
<ipython-input-49-75e65edfc8ed>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-cop

<ipython-input-49-75e65edfc8ed>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec['rating'] = 1.0
<ipython-input-49-75e65edfc8ed>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([user1, target, 1.0])
<ipython-input-49-75e65edfc8ed>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie

<ipython-input-49-75e65edfc8ed>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec['rating'] = 1.0
<ipython-input-49-75e65edfc8ed>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([user1, target, 1.0])
<ipython-input-49-75e65edfc8ed>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie

...

<ipython-input-49-75e65edfc8ed>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([user1, target, 1.0])
<ipython-input-49-75e65edfc8ed>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec['user'] = np.array(user)
<ipython-input-49-75e65edfc8ed>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-cop

<ipython-input-49-75e65edfc8ed>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([user1, target, 1.0])
<ipython-input-49-75e65edfc8ed>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec['user'] = np.array(user)
<ipython-input-49-75e65edfc8ed>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-cop

<ipython-input-49-75e65edfc8ed>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec['rating'] = 1.0
<ipython-input-49-75e65edfc8ed>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([user1, target, 1.0])
<ipython-input-49-75e65edfc8ed>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie

0.3694581280788177 0.1109355313492137 0.6978653530377669 0.17788231192981885


<ipython-input-49-75e65edfc8ed>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([user1, target, 1.0])
<ipython-input-49-75e65edfc8ed>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec['user'] = np.array(user)
<ipython-input-49-75e65edfc8ed>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-cop

In [64]:
res

[[0.6502463054187192,
  0.3726723537667068,
  0.7602627257799671,
  0.40064058495020016],
 [0.18883415435139572,
  0.0720492373652657,
  0.47619047619047616,
  0.14112889461126005],
 [0.17569786535303777,
  0.06369853120401521,
  0.4236453201970443,
  0.12168852896060106],
 [0.37766830870279144,
  0.1708298613381564,
  0.6584564860426929,
  0.24077793106102835],
 [0.2545155993431856,
  0.08866208205608161,
  0.5714285714285714,
  0.1619304353533444],
 [0.3694581280788177,
  0.1109355313492137,
  0.6978653530377669,
  0.17788231192981885]]

In [52]:
class MLP(nn.Module):
    def __init__(self, n_users, n_items, n_factors,layers):
        super(MLP, self).__init__()
        self.n_users = n_users
        self.n_items = n_items
        self.n_factors = n_factors
        self.layers = layers
        self.user_factors = torch.nn.Embedding(n_users, n_factors)
        self.item_factors = torch.nn.Embedding(n_items, n_factors)
        
        self.MLP1 = nn.Sequential(nn.Linear(2 * n_factors, self.layers[0]))
        self.MLP2 = nn.Sequential(nn.Linear(self.layers[0],self.layers[1]))
        self.MLP3 = nn.Sequential(nn.Linear(self.layers[1],self.layers[2]))
        self.MLP4 = nn.Sequential(nn.Linear(self.layers[2],self.layers[3]))
        self.outlayer = nn.Sequential(nn.Linear(self.layers[3],1))
        
    def forward(self, user_id, item_id):
        MLP_user_embeddings = self.user_factors(user_id) ## 128 * 64
        MLP_item_embeddings = self.item_factors(item_id) ## 128 * 64
        MLP_merge_embedding = torch.cat((MLP_user_embeddings,MLP_item_embeddings),1) ## 128 * 128
        
        MLP_out1 = self.MLP1(MLP_merge_embedding) ## 128 * 64
        MLP_out1 = torch.nn.ReLU()(MLP_out1)
        
        MLP_out2 = self.MLP2(MLP_out1) ## 128 * 32
        MLP_out2 = torch.nn.ReLU()(MLP_out2)
        
        MLP_out3 = self.MLP3(MLP_out2) ## 128 * 16
        MLP_out3 = torch.nn.ReLU()(MLP_out3)
        
        MLP_out4 = self.MLP4(MLP_out3) ## 128 * 8
        MLP_out4 = torch.nn.ReLU()(MLP_out4)
        
        out = self.outlayer(MLP_out4)  ## 128 * 1
        return out.squeeze(1)   

In [53]:
class GMF(nn.Module):
    def __init__(self, n_users, n_items, n_factors):
        super(GMF, self).__init__()
        self.n_users = n_users
        self.n_items = n_items
        self.n_factors = n_factors
        self.user_factors = torch.nn.Embedding(n_users, n_factors)
        self.item_factors = torch.nn.Embedding(n_items, n_factors)
        self.outlayer = nn.Sequential(nn.Linear(n_factors,1))
        
    def forward(self, user_id, item_id):
        GMF_user_embeddings = self.user_factors(user_id) ## 128 * 64
        GMF_item_embeddings = self.item_factors(item_id) ## 128 * 64
        GMF_merge_embedding = MLP_user_embeddings * MLP_item_embeddings ## 128 * 64
        
        out = self.outlayer(GMF_merge_embedding)  ## 128 * 1
        return out.squeeze(1)   

In [54]:
class NeuMF(nn.Module):
    def __init__(self, n_users, n_items, mlp_factors,gmf_factors, layers):
        super(NeuMF, self).__init__()
        self.n_users = n_users
        self.n_items = n_items
        self.mlp_factors = mlp_factors
        self.gmf_factors = gmf_factors
        self.layers = layers
        
        self.mlp_user_factors = torch.nn.Embedding(n_users, mlp_factors)
        self.mlp_item_factors = torch.nn.Embedding(n_items, mlp_factors)
        
        self.gmf_user_factors = torch.nn.Embedding(n_users, gmf_factors)
        self.gmf_item_factors = torch.nn.Embedding(n_items, gmf_factors)
        
        self.MLP1 = nn.Sequential(nn.Linear(2 * mlp_factors, self.layers[0]))
        self.MLP2 = nn.Sequential(nn.Linear(self.layers[0],self.layers[1]))
        self.MLP3 = nn.Sequential(nn.Linear(self.layers[1],self.layers[2]))
        self.MLP4 = nn.Sequential(nn.Linear(self.layers[2],self.layers[3]))
        
        self.outlayer = nn.Sequential(nn.Linear(self.layers[3] + gmf_factors,1))
        
        
    def forward(self, user_id, item_id):
        GMF_user_embeddings = self.gmf_user_factors(user_id) ## 128 * 64
        GMF_item_embeddings = self.gmf_item_factors(item_id) ## 128 * 64
        GMF_merge_embedding = GMF_user_embeddings * GMF_item_embeddings ## 128 * 64
        
        
        MLP_user_embeddings = self.mlp_user_factors(user_id) ## 128 * 64
        MLP_item_embeddings = self.mlp_item_factors(item_id) ## 128 * 64
        MLP_merge_embedding = torch.cat((MLP_user_embeddings,MLP_item_embeddings),1) ## 128 * 128
        
        
        MLP_out1 = self.MLP1(MLP_merge_embedding) ## 128 * 64
        MLP_out1 = torch.nn.ReLU()(MLP_out1)
        
        MLP_out2 = self.MLP2(MLP_out1) ## 128 * 32
        MLP_out2 = torch.nn.ReLU()(MLP_out2)
        
        MLP_out3 = self.MLP3(MLP_out2) ## 128 * 16
        MLP_out3 = torch.nn.ReLU()(MLP_out3)
        
        MLP_out4 = self.MLP4(MLP_out3) ## 128 * 8
        MLP_out4 = torch.nn.ReLU()(MLP_out4)
        
        out = torch.cat((GMF_merge_embedding,MLP_out4),1)
        
        
        out = self.outlayer(out)  ## 128 * 1
        return out.squeeze(1)   

In [55]:
def RMSE(data, model):
    users_index = data.iloc[:, 0].values
    users = torch.LongTensor(users_index).to(DEVICE)
    items_index = data.iloc[:, 1].values
    items = torch.LongTensor(items_index).to(DEVICE)
    rating = torch.FloatTensor(data.iloc[:, 5].values).to(DEVICE)
    prediction= model(users, items)
    rmse = loss_func(prediction, rating)
    mae = torch.nn.L1Loss()(prediction, rating)
    return rmse ** 0.5,mae

In [56]:
def train(lr, mlp_factors,gmf_factors, layers, reg, batch_size, num_epochs, train, test):
    model = NeuMF(n_users, n_items, mlp_factors,gmf_factors, layers).to(DEVICE)
    optimizer = torch.optim.Adam(params=model.parameters(), lr=lr,weight_decay=reg)
    scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
        optimizer, mode='min', factor=0.5, patience=10, threshold_mode='abs',threshold = 0.005)
    for epoch in range(num_epochs):
        model.train()
        t1 = time.time()
        num_example = len(train)
        indices = list(range(num_example))
        for i in tqdm(range(0, num_example, batch_size)):
            optimizer.zero_grad()
            indexs = indices[i:min(i+batch_size, num_example)]
            users_index = train.iloc[:, 0].loc[indexs].values
            users = torch.LongTensor(users_index).to(DEVICE)
            items_index = train.iloc[:, 1].loc[indexs].values
            items = torch.LongTensor(items_index).to(DEVICE)
            
           
            rating = torch.FloatTensor(
                train.iloc[:, 5].loc[indexs].values).to(DEVICE)
            prediction = model(
                users, items)

            err = loss_func(prediction, rating) 
            err.backward()
            optimizer.step()
        t2 = time.time()
        rmse, mae = RMSE(test, model)
        scheduler.step(rmse)
        print("Epoch: ", epoch, " Loss: ", err, " RMSE in test set:",
              rmse, "MAE in test set: ", mae)
        print("Time consumed is:", t2-t1)
    return model

In [57]:
lr = 0.002
mlp_factors = 8
gmf_factors = 32 
layers = [64,32,16,8]
reg = 1e-6
batch_size = 128 
num_epochs = 100


In [58]:
n_users = len(hehe['user_id'].value_counts())
n_items = len(hehe['movie'].value_counts())

In [59]:
model_neumf = train(lr, mlp_factors,gmf_factors, layers, reg, batch_size, num_epochs, hehe_test,df_empty)

100%|██████████| 785/785 [00:03<00:00, 218.94it/s]


Epoch:  0  Loss:  tensor(0.9409, grad_fn=<MseLossBackward0>)  RMSE in test set: tensor(0.9965, grad_fn=<PowBackward0>) MAE in test set:  tensor(0.8419, grad_fn=<L1LossBackward0>)
Time consumed is: 3.588245391845703


100%|██████████| 785/785 [00:03<00:00, 220.13it/s]


Epoch:  1  Loss:  tensor(0.8912, grad_fn=<MseLossBackward0>)  RMSE in test set: tensor(0.9110, grad_fn=<PowBackward0>) MAE in test set:  tensor(0.7659, grad_fn=<L1LossBackward0>)
Time consumed is: 3.5704448223114014


100%|██████████| 785/785 [00:03<00:00, 206.12it/s]


...

Epoch:  97  Loss:  tensor(0.0032, grad_fn=<MseLossBackward0>)  RMSE in test set: tensor(0.1193, grad_fn=<PowBackward0>) MAE in test set:  tensor(0.0761, grad_fn=<L1LossBackward0>)
Time consumed is: 3.574594497680664


100%|██████████| 785/785 [00:03<00:00, 220.51it/s]


Epoch:  98  Loss:  tensor(0.0002, grad_fn=<MseLossBackward0>)  RMSE in test set: tensor(0.1113, grad_fn=<PowBackward0>) MAE in test set:  tensor(0.0624, grad_fn=<L1LossBackward0>)
Time consumed is: 3.564072608947754


100%|██████████| 785/785 [00:03<00:00, 221.28it/s]

Epoch:  99  Loss:  tensor(0.0003, grad_fn=<MseLossBackward0>)  RMSE in test set: tensor(0.1126, grad_fn=<PowBackward0>) MAE in test set:  tensor(0.0620, grad_fn=<L1LossBackward0>)
Time consumed is: 3.5519516468048096


In [60]:
num_i = 101
def get_prediction_list(model,user,target,actors_id,directors_id,genres_id,k):
    item_neg = user_item_neg[user]
    movie_rec = movie[movie['movie'].isin(item_neg)]
    movie_rec.index = range(1, len(movie_rec)+1)
    movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
    user = np.array([user] * num_i)
    users = torch.LongTensor(user).to(DEVICE)
    items = movie_rec['movie'].values
    items = torch.LongTensor(items).to(DEVICE)
    
    prediction = model(
                users, items)
    prediction = prediction.detach().numpy()
    prediction = np.maximum(prediction, np.ones(num_i) * 0)  # bound the lower values
    prediction = np.minimum(prediction, np.ones(num_i) * 5)
    prediction_dict = dict(zip(movie_rec['movie'].values, prediction))
    top_k = dic_order_value_and_get_key(prediction_dict,k)
    return top_k,prediction_dict

In [61]:
import math
def hr_ndcg(data,model):
    hr1 = 0.0
    ndcg1 = 0.0
    hr2 = 0.0
    ndcg2 = 0.0
    test_eva_dict = data.to_dict('records')
    for row in test_eva_dict[:]:
        user = row['user_id']
        target = row['movie']
        actors_id = row['actors']
        directors_id = row['director']
        genres_id = row['genre']
        
        
        recommended_item_10,_ = get_prediction_list(model,user,target,actors_id,directors_id,genres_id,10)
        recommended_item_20,_ = get_prediction_list(model,user,target,actors_id,directors_id,genres_id,20)
        if target in recommended_item_10:
            hr1 +=1
            posi = recommended_item_10.index(target)
            ndcg1 += 1 / math.log(posi + 2,2)
        if target in recommended_item_20:
            hr2 +=1
            posi = recommended_item_20.index(target)
            ndcg2 += 1 / math.log(posi + 2,2)
    return hr1 / data.shape[0], ndcg1 / data.shape[0],hr2 / data.shape[0], ndcg2 / data.shape[0]
        

In [62]:
hr_ndcg(df_empty,model_neumf)

<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when cr

<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc

<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when cr

<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc

<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc

...

<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc

<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when cr

<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc

<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  movie_rec.loc[0] = np.array([target, actors_id, directors_id, genres_id])
<ipython-input-60-412ae19070fc>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_rec.loc

(0.7865353037766831,
 0.4075809236411896,
 0.9425287356321839,
 0.4467881592146901)

In [63]:
state = {'model': model.state_dict()}
torch.save(state, '/home/jinfeng/Downloads/doctorant/Conférences/dsaa/argumrntative/KR2020-Aspect-Item-Recommender-System-master/data/MOVIELENS/ml-latest-small/new_models/model_.pkl')
qnm.append(cnm)